## Case 1 - Deterministic
## Case 2 - DRO opt w/o $\gamma$
## Case 3 - DRO opt w $\gamma$
## Case 4 - DRO opt w DRJCC
## Case 5 - DRO opt DRJCC with ESS reserve
## Case 6 - DRO opt DRJCC with ESS reserve but without revenue
### Author: Junhyeok Kim

In [1]:
# Import the library

import os
import pandas as pd
import numpy as np
import sys
import time

import matplotlib.pyplot as plt
np.set_printoptions(formatter={'float': '{: 0.6f}'.format})

In [2]:
# Define the Variables
BASE_DIR = os.getcwd()
os.chdir("../")
path = os.getcwd() 
sys.path.append(path) # 폴더 한 단계 위에서 file import 하기 위해서 sys path 설정
sys.path.append(f"{path}/src")
sys.path.append(f"{path}/src/Data_Generation")

from rts_data import generate_wind, generate_gen_dict
from aggregator import aggregator
from gurobiMILP import gurobi_MILP, oos_test
from draw_fig import Single_Case_Plot
from different_approach import gurobi_simulation

In [3]:
### Parameters
DRO_param = {'eps_joint_cvar' : 0.05}
DRO_param['theta'] = 0.05

# Vector for Bonferroni approximation
rho_vectorC = np.linspace(0, 0.0025, 26)

# Number of individual runs (number of coupled datasets in the numerical study)

IR_max = 100


# Number of maximum sample size (N)

N_max = 1000

# Number of maximum out of sample data for each individual run (N') for testing
# dataset
OOS_max = 1000

# Number of sample data in training dataset (N)

N = 100;


# Total number of data 

n_total_scen = IR_max * (N_max + OOS_max)

In [4]:
# Define the Parameters

# case_dict: Generate various scenario
# res_var: Define the WT and PV as variables [True] or parameters [False]
# case:
    # case 1 : w/o uncertainty
    # case 2 : w uncertainty with DRO
    #UNIT_TIME: 1 -> 1 hour
    
case_dict = {'case':6, 'UNIT_TIME': 1, 'bid_type':'deterministic', 'n_total_scen': n_total_scen, 'N_max': N_max, 'OOS_max':OOS_max,
             'IR_max': IR_max, 'N': N, 'divide_factor': 1}

case_dict['date'] = '20220911'

nTimeslot = int(24 / case_dict['UNIT_TIME'])
char_ess = {'initSOC':0.5, 'termSOC':0.5, 'minSOC':0.2, 'maxSOC':0.8, 'efficiency':0.95}


model_dict = {'nVPP':1, 'path': path, 'N_PIECE': 10, 'nTimeslot': nTimeslot}

# Once, set te PV, WT, SMP uncertainties identically in each time (PV: 5%, WT: 10%, SMP: 10%)
uncertainty_dict = {'pv': np.ones(nTimeslot)*0.10 , 'wt': np.ones(nTimeslot)*0.10, 'smp':np.ones(nTimeslot)*0.10}


if case_dict['case']==2:
    
    model_dict['uncertainty'] = uncertainty_dict
    case_dict['bid_type'] = 'risky'
    
elif case_dict['case'] == 1:
    
    uncertainty_dict = {'pv': np.zeros(nTimeslot), 'wt': np.zeros(nTimeslot), 'smp':np.zeros(nTimeslot)}
    model_dict['uncertainty'] = uncertainty_dict
    

In [5]:
# Set Up VPP  #Unit: kW

vpp_list = []
for i in range(model_dict['nVPP']):
    nGen_dict = {'WT':4,'PV':2, 'ESS':1, 'DG':2}
    wt_list = [800, 700, 900, 1000]
    pv_list = [500, 750, 500, 700]
    ess_list = [300]
    capacity_list = [1500]
    dg_list = [300, 400, 900]
    max_list = [wt_list, pv_list, ess_list, capacity_list, dg_list]
    
    dg_dict_list = []
    for j in range(nGen_dict['DG']):
        dg_dict_list.append(generate_gen_dict(j,dg_list[j], model_dict))
    model_dict['dg_dict_list'] = dg_dict_list
    
    agg_dict = {'name': f'cvpp{i+1}', 'code': f'xds{i+1}', 'gen':nGen_dict}
    vpp_list.append(aggregator(agg_dict, char_ess, model_dict, case_dict))
    vpp_list[i].set_der_power(max_list)
    vpp_list[i].set_smp_data(case_dict['date'])
    vpp_list[i].set_profile(case_dict['N'],0)
vpp_list[0].get_res_table()

Error
'aggregator' object has no attribute 'wt_uncert'
Aggregator set_res_table method
Uncertainty does not exist


name type  number  min_power  max_power  capacity
0   WT1_cvpp1   WT       1        0.0        800       NaN
1   WT2_cvpp1   WT       2        0.0        700       NaN
2   WT3_cvpp1   WT       3        0.0        900       NaN
3   WT4_cvpp1   WT       4        0.0       1000       NaN
4   PV5_cvpp1   PV       5        0.0        500       NaN
5   PV6_cvpp1   PV       6        0.0        750       NaN
6  ESS7_cvpp1  ESS       7     -300.0        300    1500.0
7   DG8_cvpp1   DG       8       30.0        300       NaN
8   DG9_cvpp1   DG       9       40.0        400       NaN

In [11]:
vpp_list[0].res_list[0].profile_xi[0,0]

-165.6886833981855

In [20]:
case_dict['case'] = 2
Wmax = vpp_list[0].wt_list[0].max_power 
Wmu = vpp_list[0].wt_list[0].profile_mu
#case_dict['theta'] = DRO_param['theta']* Wmu
#case_dict['theta'] = np.reshape(case_dict['theta'], -1)
case_dict['theta'] = [DRO_param['theta']] * nTimeslot
case_dict['eps'] = DRO_param['eps_joint_cvar']
case_dict['beta'] = 0.1
case_dict['alpha_max'] = 0.2
case_dict['GRID_PIECE'] = 100

OOS_sim = 100
OOS_iter = int(OOS_max / OOS_sim)

IIS_sim = 50
IIS_iter = int(N_max/IIS_sim)
ratio_list = []
mip_gap = 0.0001
feas_tol = 1e-4
vpp = vpp_list[0]    

start_time = time.time()
total_WDRCC_result = []
total_SAA_result = []
total_robust_result = []
total_moment_result = []
total_ratio_list = []
for i in range(IIS_iter):
    WDRCC_result = []
    SAA_result = []
    robust_result = []
    moment_result = []
    ratio_list = []
    for j in range(IR_max):
        print("****************")
        print("Iteration i, j is :", i, j)
        print("****************")
        
        N = (i+1)* IIS_sim
        case_dict['N'] = N
        vpp_list[0].set_profile(N,j)
    
        case_dict['case'] = 6
        opt_bid_WDRCC = gurobi_MILP('opt bid_wdrcc', vpp_list[0], model_dict, case_dict)
        
        case_dict['case'] = 'SAA'
        opt_bid_SAA = gurobi_simulation('opt bid_SAA', vpp_list[0], model_dict, case_dict)
        
        case_dict['case'] = 'robust'
        opt_bid_robust = gurobi_simulation('opt bid_robust', vpp_list[0], model_dict, case_dict)
        case_dict['case'] = 'momentDRO'
        #opt_bid_momentDRO = gurobi_simulation('opt bid_momentDRO', vpp_list[0], model_dict, case_dict)
        
        sol_WDRCC, obj_dict_WDRCC, P_dict_WDRCC, U_dict_WDRCC, slack_dict_WDRCC = opt_bid_WDRCC.optimize(mip_gap, feas_tol)
        sol_SAA, obj_dict_SAA, P_dict_SAA, U_dict_SAA, slack_dict_SAA = opt_bid_SAA.optimize(mip_gap, feas_tol)    
        sol_robust, obj_dict_robust, P_dict_robust, U_dict_robust, slack_dict_robust = opt_bid_robust.optimize(mip_gap, feas_tol)
        #sol_momentDRO, obj_dict_momentDRO, P_dict_momentDRO, U_dict_momentDRO, slack_dict_momentDRO = opt_bid_momentDRO.optimize(mip_gap, feas_tol)

        WDRCC_result.append([sol_WDRCC, obj_dict_WDRCC, P_dict_WDRCC, U_dict_WDRCC, slack_dict_WDRCC, 
                             opt_bid_WDRCC.m.objVal,opt_bid_WDRCC.opt_solve_time, opt_bid_WDRCC])
        SAA_result.append([sol_SAA, obj_dict_SAA, P_dict_SAA, U_dict_SAA, slack_dict_SAA, 
                           opt_bid_SAA.m.objVal, opt_bid_SAA.opt_solve_time,  opt_bid_SAA ])
        robust_result.append([sol_robust, obj_dict_robust, P_dict_robust, U_dict_robust, slack_dict_robust, 
                              opt_bid_robust.m.objVal, opt_bid_robust.opt_solve_time, opt_bid_robust])
        #moment_result.append([sol_momentDRO, obj_dict_momentDRO, P_dict_momentDRO, U_dict_momentDRO, slack_dict_momentDRO,
        #                      opt_bid_momentDRO.m.objVal,opt_bid_momentDRO.opt_solve_time,opt_bid_momentDRO])
        
        ratio_wdrcc_list = []
        ratio_SAA_list = []
        ratio_robust_list = []
        ratio_momentDRO_list = []
        check_array_wdrcc_list = []
        check_array_SAA_list = []
        check_array_robust_list = []
        check_array_momentDRO_list = []
        for k in range(OOS_iter):
            nOOS = (k+1)*OOS_sim
            # OOS_sim
            
            lhs_array, rhs_array, check_wdrcc_array, ratio_wdrcc = oos_test(opt_bid_WDRCC, vpp, nOOS)
            ratio_wdrcc_list.append(ratio_wdrcc)
            
            oos_lhs_array, oos_rhs_array, oos_SAA_check_array, ratio_SAA = oos_test(opt_bid_SAA, vpp, nOOS)
            ratio_SAA_list.append(ratio_SAA)

            oos_lhs_array, oos_rhs_array, oos_robust_check_array, ratio_robust = oos_test(opt_bid_robust, vpp, nOOS)
            ratio_robust_list.append(ratio_robust)

            #oos_lhs_array, oos_rhs_array, oos_momentDRO_check_array, ratio_momentDRO = oos_test(opt_bid_momentDRO, vpp, nOOS)
            #ratio_momentDRO_list.append(ratio_momentDRO)
            
            check_array_wdrcc_list.append(sum(check_wdrcc_array))
            check_array_SAA_list.append(sum(oos_SAA_check_array))
            check_array_robust_list.append(sum(oos_robust_check_array))
            #check_array_momentDRO_list.append(sum(oos_momentDRO_check_array))

        ratio_list.append([ratio_wdrcc_list, ratio_SAA_list, ratio_robust_list, ratio_momentDRO_list])
        
        
        
    total_WDRCC_result.append(WDRCC_result)
    total_SAA_result.append(SAA_result)
    total_robust_result.append(robust_result)
    total_moment_result.append(moment_result)
    total_ratio_list.append(ratio_list)
end_time = time.time()
total_solution_time = end_time - start_time

****************
Iteration i, j is : 0 0
****************
Does not Cosidered alpha
Add Bid Constraint
start set_dro_obj_constriants
end set_dro_obj_constriants
start drjcc
iteration 0 of sum drjcc
iteration 5 of sum drjcc
iteration 10 of sum drjcc
iteration 15 of sum drjcc
iteration 20 of sum drjcc
finish max constraint of DRJCC
start set_base_objectives
end set_base_objectives
Set parameter FeasibilityTol to value 0.0001
Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (win64)

CPU model: 12th Gen Intel(R) Core(TM) i5-12400, instruction set [SSE2|AVX|AVX2]
Thread count: 6 physical cores, 12 logical processors, using up to 12 threads

Optimize a model with 12547 rows, 28992 columns and 55878 nonzeros
Model fingerprint: 0x1cfe1607
Model has 2400 general constraints
Variable types: 28800 continuous, 192 integer (192 binary)
Coefficient statistics:
  Matrix range     [3e-05, 1e+03]
  Objective range  [2e-02, 5e+03]
  Bounds range     [1e+00, 1e+07]
  RHS range        [4e-02, 2e+05]
Presol

     0     0 3649245.99    0   62 3622148.15 3649245.99  0.75%     -    2s
     0     0 3647784.30    0   59 3622148.15 3647784.30  0.71%     -    2s
     0     0 3645216.80    0   53 3622148.15 3645216.80  0.64%     -    2s
     0     0 3644303.96    0   51 3622148.15 3644303.96  0.61%     -    2s
     0     0 3643048.13    0   39 3622148.15 3643048.13  0.58%     -    2s
     0     0 3643048.13    0   39 3622148.15 3643048.13  0.58%     -    2s
H    0     0                    3629657.9266 3643048.13  0.37%     -    2s
     0     0 3642267.22    0   37 3629657.93 3642267.22  0.35%     -    2s
     0     0 3641987.64    0   36 3629657.93 3641987.64  0.34%     -    2s
H    0     0                    3632329.4591 3641987.64  0.27%     -    2s
     0     0 3635070.73    0   20 3632329.46 3635070.73  0.08%     -    2s
     0     0 3634619.04    0   19 3632329.46 3634619.04  0.06%     -    2s
     0     0 3632839.62    0    6 3632329.46 3632839.62  0.01%     -    2s
     0     0 3632838.58  

Model fingerprint: 0x31a69ac6
Model has 2400 general constraints
Variable types: 28800 continuous, 192 integer (192 binary)
Coefficient statistics:
  Matrix range     [6e-04, 1e+03]
  Objective range  [2e-02, 5e+03]
  Bounds range     [1e+00, 1e+07]
  RHS range        [1e-01, 2e+05]
Presolve removed 9346 rows and 25425 columns
Presolve time: 0.11s
Presolved: 3201 rows, 3567 columns, 14530 nonzeros
Variable types: 2893 continuous, 674 integer (674 binary)

Root relaxation: objective 4.043853e+06, 1495 iterations, 0.01 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0 4043853.28    0  389          - 4043853.28      -     -    0s
     0     0 4038925.77    0  383          - 4038925.77      -     -    0s
     0     0 3981869.72    0  265          - 3981869.72      -     -    0s
     0     0 3972752.39    0  203          - 3972752.39      -     -    0s

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (win64)

CPU model: 12th Gen Intel(R) Core(TM) i5-12400, instruction set [SSE2|AVX|AVX2]
Thread count: 6 physical cores, 12 logical processors, using up to 12 threads

Optimize a model with 2947 rows, 4512 columns and 16254 nonzeros
Model fingerprint: 0x635a18b6
Variable types: 3120 continuous, 1392 integer (1392 binary)
Coefficient statistics:
  Matrix range     [6e-04, 1e+06]
  Objective range  [2e-02, 5e+03]
  Bounds range     [1e+00, 1e+06]
  RHS range        [1e-01, 2e+05]
Presolve removed 1966 rows and 3189 columns
Presolve time: 0.01s
Presolved: 981 rows, 1323 columns, 9566 nonzeros
Variable types: 649 continuous, 674 integer (674 binary)
Found heuristic solution: objective 4922758.1085

Root relaxation: objective 5.031002e+06, 232 iterations, 0.00 seconds (0.00 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0 

  RHS range        [2e-01, 2e+05]
Presolve removed 9367 rows and 25446 columns
Presolve time: 0.11s
Presolved: 3180 rows, 3546 columns, 14469 nonzeros
Variable types: 2879 continuous, 667 integer (667 binary)

Root relaxation: objective 4.011862e+06, 1338 iterations, 0.01 seconds (0.01 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0 4011862.33    0  404          - 4011862.33      -     -    0s
     0     0 3999158.40    0  402          - 3999158.40      -     -    0s
     0     0 3898980.51    0  245          - 3898980.51      -     -    0s
     0     0 3898109.24    0  211          - 3898109.24      -     -    0s
     0     0 3896993.48    0  203          - 3896993.48      -     -    0s
     0     0 3893330.53    0  200          - 3893330.53      -     -    0s
     0     0 3893330.53    0  199          - 3893330.53      -     -    0s
     0     0 3868329.69 

...

     0     0 3797395.38    0  192 3647453.15 3797395.38  4.11%     -    2s
H    0     0                    3658860.5839 3797395.38  3.79%     -    2s
     0     0 3796317.00    0  192 3658860.58 3796317.00  3.76%     -    2s
     0     0 3793950.29    0  184 3658860.58 3793950.29  3.69%     -    2s
     0     0 3793667.99    0  186 3658860.58 3793667.99  3.68%     -    2s
     0     0 3793585.50    0  188 3658860.58 3793585.50  3.68%     -    2s
     0     0 3793580.61    0  188 3658860.58 3793580.61  3.68%     -    2s
     0     0 3792067.36    0  181 3658860.58 3792067.36  3.64%     -    2s
     0     0 3781122.36    0  172 3658860.58 3781122.36  3.34%     -    2s
     0     0 3780856.84    0  176 3658860.58 3780856.84  3.33%     -    2s
     0     0 3780726.99    0  178 3658860.58 3780726.99  3.33%     -    2s
     0     0 3780709.58    0  178 3658860.58 3780709.58  3.33%     -    2s
     0     0 3779851.72    0  175 3658860.58 3779851.72  3.31%     -    2s
     0     0 3779793.88  

     0     0 5030639.41    0   80 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   80 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   83 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   87 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.37    0   89 5025830.40 5030639.37  0.10%     -    0s
     0     0 5030554.28    0   70 5025830.40 5030554.28  0.09%     -    0s
H    0     0                    5026361.0759 5030554.28  0.08%     -    0s
     0     0 5030518.20    0   71 5026361.08 5030518.20  0.08%     -    0s
     0     0 5030322.72    0   58 5026361.08 5030322.72  0.08%     -    0s
     0     0 5030302.99    0   62 5026361.08 5030302.99  0.08%     -    0s
     0     0 5030296.81    0   59 5026361.08 5030296.81  0.08%     -    0s
     0     0 5030296.32    0   61 5026361.08 5030296.32  0.08%     -    0s
     0     0 5030065.99    0   55 5026361.08 5030065.99  0.07%     -    0s
     0     0 5030048.96  

     0     0 5030639.41    0   89 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   89 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   59 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   66 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   80 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   80 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   83 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.41    0   87 5025830.40 5030639.41  0.10%     -    0s
     0     0 5030639.37    0   89 5025830.40 5030639.37  0.10%     -    0s
     0     0 5030554.28    0   70 5025830.40 5030554.28  0.09%     -    0s
H    0     0                    5026361.0759 5030554.28  0.08%     -    0s
     0     0 5030518.20    0   71 5026361.08 5030518.20  0.08%     -    0s
     0     0 5030322.72    0   58 5026361.08 5030322.72  0.08%     -    0s
     0     0 5030302.99  

     0     0 3717675.74    0  166 3523479.48 3717675.74  5.51%     -    2s
     0     0 3717160.86    0  169 3523479.48 3717160.86  5.50%     -    2s
     0     0 3717080.30    0  163 3523479.48 3717080.30  5.49%     -    2s
     0     0 3716937.97    0  161 3523479.48 3716937.97  5.49%     -    2s
     0     0 3716920.59    0  159 3523479.48 3716920.59  5.49%     -    2s
     0     0 3716392.53    0  161 3523479.48 3716392.53  5.48%     -    2s
     0     0 3712241.67    0  162 3523479.48 3712241.67  5.36%     -    2s
     0     2 3711550.27    0  158 3523479.48 3711550.27  5.34%     -    3s

Cutting planes:
  Learned: 7
  Gomory: 11
  Cover: 105
  Implied bound: 587
  Clique: 2
  MIR: 166
  Flow cover: 399
  Inf proof: 2
  Zero half: 2
  Network: 10
  RLT: 20
  Relax-and-lift: 81
  BQP: 1
  PSD: 5

Explored 1162 nodes (57339 simplex iterations) in 4.50 seconds (4.30 work units)
Thread count was 12 (of 12 available processors)

Solution count 1: 3.52348e+06 

Solve interrupted (error 

GurobiError: Out of memory

In [12]:
vpp_list[0].set_profile(N,j)

In [14]:
vpp_list[0].wt_list[0].profile_xi.shape

(24, 50)

In [ ]:
vpp_list[0].wt_list[0].oos_profile

In [ ]:
# Gurobi Optimization Model
case_dict['case'] = 2
Wmax = vpp_list[0].wt_list[0].max_power 
Wmu = vpp_list[0].wt_list[0].profile_mu
#case_dict['theta'] = DRO_param['theta']* Wmu
#case_dict['theta'] = np.reshape(case_dict['theta'], -1)
case_dict['theta'] = [DRO_param['theta']] * nTimeslot
case_dict['eps'] = DRO_param['eps_joint_cvar']
case_dict['beta'] = 0.1
case_dict['alpha_max'] = 0.2
case_dict['GRID_PIECE'] = 100
opt_bid_SAA = gurobi_SAA('opt bid_SAA', vpp_list[0], model_dict, case_dict)

mip_gap = 0.0001
feas_tol = 1e-4
sol_SAA, obj_dict_SAA, P_dict_SAA, U_dict_SAA, slack_dict_SAA = opt_bid_SAA.optimize(mip_gap, feas_tol)

In [ ]:
# Gurobi Optimization Model

#case_dict['theta'] = np.array([0.05]*24)
case_dict['case'] = 6
opt_bid = gurobi_MILP('opt bid', vpp_list[0], model_dict, case_dict)

mip_gap = 0.0001
feas_tol = 1e-4
sol, obj_dict, P_dict, U_dict, slack_dict = opt_bid.optimize(mip_gap, feas_tol)

In [ ]:
obj1 = obj_dict['obj1']
print(obj1)

try:
    obj2 = obj_dict['obj2']
    obj3 = obj_dict['obj3']
    print(obj2)
    print(obj3)
    
except:
    print("no obj2, obj3")

try:
    obj3_full = obj_dict['obj3_full']
except:
    pass
print(sum(obj1))
print(sum(obj2))
print(sum(obj3))

print(sum(sum(obj_dict['dg_cost'])))

print(opt_bid.m.objVal)

In [ ]:
print(P_dict['sum_dg'])

if opt_bid.is_dg_reserve:
    print(P_dict['dg_ru'])

In [ ]:
print(P_dict['essDis'])
print(P_dict['essChg'])
if opt_bid.is_ess_reserve:
    print(P_dict['RU_essdis'])
    print(P_dict['RD_esschg'])

In [ ]:
if opt_bid.is_bid_DRCC:
    lhs_array, rhs_array, check_array, ratio = opt_bid.check_drcc_constraint()
    print("Ratio is :", ratio)
    for i in range(24):
        print(sum(check_array[i,:]))

In [ ]:
if opt_bid.is_bid_DRCC:
    oos_lhs_array, oos_rhs_array, oos_check_array, oos_ratio = opt_bid.oos_test()
    print("Ratio is :", oos_ratio)
    for i in range(24):
        print(sum(oos_check_array[i,:]))

In [ ]:
oos_lhs_array1, oos_rhs_array1, oos_check_array1, oos_ratio1 = opt_bid_SAA.oos_test()
print("Ratio is :", oos_ratio1)
for i in range(24):
    print(sum(oos_check_array1[i,:]))

In [ ]:
opt_bid.res_list[i].oos_profile_xi.shape

In [ ]:
from draw_fig import Single_Case_Plot

In [ ]:
case_fig = Single_Case_Plot(vpp_list, opt_bid, model_dict, case_dict, path)

In [ ]:
case_fig_SAA = Single_Case_Plot(vpp_list, opt_bid_SAA, model_dict, case_dict, path)

In [ ]:
case_fig_SAA.make_plot(P_dict_SAA, slack_dict_SAA, save_flag=True)

In [ ]:
if opt_bid_SAA.is_ess_reserve or opt_bid_SAA.is_dg_reserve:
    case_fig_SAA.make_reserve_plot(P_dict_SAA, save_flag=True)

In [ ]:
case_fig.make_plot(P_dict, slack_dict, save_flag=True)

In [ ]:
if opt_bid.is_ess_reserve or opt_bid.is_dg_reserve:
    case_fig.make_reserve_plot(P_dict, save_flag=True)

In [ ]:
for j in range(IR_sim):
    print(f"out of sample iteration: {j}")
    print(f"out of sample iteration: {j}")
    print(f"out of sample iteration: {j}")
    opt_bid_SAA = gurobi_SAA('opt bid_SAA', vpp_list[0], model_dict, case_dict)


    sol_SAA, obj_dict_SAA, P_dict_SAA, U_dict_SAA, slack_dict_SAA = opt_bid_SAA.optimize(mip_gap, feas_tol)
    for k in range(OOS_sim):
        
            